<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Data Processing

In this workflow within PyCCAPT, we can crope the data, do the voltage and bowl calibration, calculate the 3d reconstruction, and do the ranging.
</div>

In [1]:
# Activate intractive functionality of matplotlib
# Activate intractive functionality of matplotlib
%matplotlib ipympl
# Activate auto reload 
%load_ext autoreload
%autoreload 2
%reload_ext autoreload
# import libraries
import os
import numpy as np
from ipywidgets import fixed
from ipywidgets import interact_manual
from ipywidgets import widgets
from IPython.display import display
import warnings
# Ignore all warnings
warnings.filterwarnings("ignore")

# Local module and scripts
from pyccapt.calibration.calibration_tools import tools, share_variables
from pyccapt.calibration.calibration_tools import widgets as wd
from pyccapt.calibration.data_tools import data_tools, data_loadcrop, dataset_path_qt
from pyccapt.calibration.mc import mc_tools, tof_tools
from pyccapt.calibration.calibration_tools import mc_plot
from pyccapt.calibration.tutorials.tutorials_helper import helper_voltage_bowl
from pyccapt.calibration.tutorials.tutorials_helper import helper_data_loader
from pyccapt.calibration.tutorials.tutorials_helper import helper_temporal_crop
from pyccapt.calibration.tutorials.tutorials_helper import helper_special_crop
from pyccapt.calibration.tutorials.tutorials_helper import helper_t_0_tune
from pyccapt.calibration.tutorials.tutorials_helper import helper_mc_plot
from pyccapt.calibration.tutorials.tutorials_helper import helper_3d_reconstruction
from pyccapt.calibration.tutorials.tutorials_helper import helper_ion_selection
from pyccapt.calibration.tutorials.tutorials_helper import helper_visualization
from pyccapt.calibration.tutorials.tutorials_helper import helper_ion_list

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
In case of recieving the error about pytable library, please install the pytables library by running the cell below. Befor running the cell, uncomment the cell by removing the # sign at the begining of the cell.
</div>


In [2]:
# check pytables library and install it
# try:
#     import tables
# except:
#     !conda install --yes --prefix {sys.prefix} pytables

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
By clicking on the button below, you can select the dataset file you want to crop. The dataset file can be in various formats, including HDF5, EPOS, POS, ATO, and CSV. The cropped data will be saved in the same directory as the original dataset file in a new directory nammed load_crop. The name of the cropped dataset file will be the same as the original dataset file. The figures will be saved in the same directory as the dataset file.
</div>

In [3]:
button = widgets.Button(
    description='load dataset',
)
@button.on_click
def open_file_on_click(b):
    """
    Event handler for button click event.
    Prompts the user to select a dataset file and stores the selected file path in the global variable dataset_path.
    """
    global dataset_path
    dataset_path = dataset_path_qt.gui_fname().decode('ASCII')
button

Button(description='load dataset', style=ButtonStyle())

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## ROI Selection and Data Cropping Workflow
    

</div>



<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

    
From the dropdown lists below, you can select the instrument specifications of the dataset. The instrument specifications are the same as the ones used for the calibration process. Data mode is specify the dataset structure. The dataset can be in raw or calibrated mode. The flight path length is the distance between the sample and the detector. The t0 is the time of flight of the ions with the lowest mass-to-charge ratio. The maximum mass-to-charge ratio is the maximum mass-to-charge ratio of tat you want to plot. You can also change it in te related cells. The detector diameter is the diameter of the detector.
</div>


In [4]:
# create object for selection of instrument specifications of the dataset
tdc, pulse_mode, flight_path_length, t0, max_mc, det_diam = wd.dataset_instrument_specification_selection()

# Display lists and comboboxes to selected instrument specifications
display(tdc, pulse_mode, flight_path_length, t0, max_mc)

Dropdown(description='Data mode:', options=('PyCCAPT', 'leap_epos', 'leap_pos', 'ato_v6'), value='PyCCAPT')

Dropdown(description='Pulse mode:', options=('voltage', 'laser'), value='voltage')

FloatText(value=110.0, description='Flight path length:')

FloatText(value=38.0, description='t0:')

FloatText(value=400.0, description='Max mc:')

In [5]:
variables = helper_data_loader.load_data(dataset_path, max_mc, flight_path_length, pulse_mode, tdc)

The maximum possible TOF is: 5010 ns
The data will be saved on the path: C:/Users/mehrp/PycharmProjects/pyccapt/tests/data/data_1642_Aug-30-2023_16-05_Al_test4/data_processing/
The dataset name after saving is: data_1642_Aug-30-2023_16-05_Al_test4
The figures will be saved on the path: C:/Users/mehrp/PycharmProjects/pyccapt/tests/data/data_1642_Aug-30-2023_16-05_Al_test4/data_processing/
{'apt': ['high_voltage', 'hour', 'main_chamber_vacuum', 'minute', 'num_events', 'pulse', 'second', 'temperature', 'time_counter'], 'dld': ['high_voltage', 'pulse', 'start_counter', 't', 'x', 'y'], 'tdc': ['channel', 'high_voltage', 'pulse', 'start_counter', 'time_data'], 'time': []}
The number of data over max_tof: 242
Total number of Ions: 12312754


In [6]:
variables.data

high_voltage (V)   pulse  start_counter       t (ns)  x_det (cm)  \
0               600.000000   328.0           8202  2537.802979    1.080816   
1               615.000000   328.0          14741  3686.929443    1.443265   
2               624.979980   328.0           2657  3110.466553   -0.688980   
3               624.979980   328.0           4568  1171.380737    0.192653   
4               634.919983   328.0           4498  2703.307129    0.058776   
...                    ...     ...            ...          ...         ...   
12312749       8000.000000  1600.0          11089  3722.090332    2.282449   
12312750       8000.000000  1600.0          13935  3065.292725    3.725714   
12312751       8000.000000  1600.0           2722  2561.627686    3.229388   
12312752       8000.000000  1600.0           3387  3579.656494    0.414694   
12312753       8000.000000  1600.0          14288  2206.904297    1.244082   

          y_det (cm)  
0           0.006531  
1          -1.812245  
2          -2.249796  
3          -0.914286  
4           1.479184  
...              ...  
12312749    2.798367  
12312750   -0.675918  
12312751    1.573878  
12312752    2.693877  
12312753   -2.847347  

[12312754 rows x 6 columns]

<div style="margin: 0 auto; padding: 20px;">

# Temporal crop

Select the data by drawing a rectangle over the experiment history. Experiment history is a 2D histogram of the time of flight of the ions versus sequence of evaporation. The experiment history is plotted by clicking on the button below te cell.
</div>


In [7]:
helper_temporal_crop.call_plot_crop_experiment(variables)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

# Spacial crop

Select the region of maximum concentration of Ions in the below plotted graph to utilize relevant data. To crop you can draw a circle over the filed desorption map. The field desorption map is a 2D histogram of the time of flight of the ions versus the position of the ions on the detector. The field desorption map is plotted by clicking on the button below the cell.
</div>

In [8]:
helper_special_crop.call_plot_crop_fdm(variables)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Calculate pulses since the last event pulse and ions per pulse. The percentage of loss in ROI selection process will be printed.
</div>

In [9]:
pulse_pi, ion_pp = data_loadcrop.calculate_ppi_and_ipp(variables.data)

# add two calculated array to the croped dataset
variables.data['pulse_pi'] = pulse_pi.astype(np.uintc)
variables.data['ion_pp'] = ion_pp.astype(np.uintc)

# exctract needed data from Pandas data frame as an numpy array
variables.dld_high_voltage = variables.data['high_voltage (V)'].to_numpy()
variables.dld_pulse = variables.data['pulse'].to_numpy()
variables.dld_t = variables.data['t (ns)'].to_numpy()
variables.dld_x_det = variables.data['x_det (cm)'].to_numpy()
variables.dld_y_det = variables.data['y_det (cm)'].to_numpy()

# save the cropped data
print('tof Crop Loss {:.2f} %'.format((100 - (len(variables.data) / len(variables.data)) * 100)))
#percentage of double event per pulse
print('percentage of double event per pulse', len(ion_pp[ion_pp != 1]) / float(len(ion_pp)))

tof Crop Loss 0.00 %
percentage of double event per pulse 0.01827020763889472


<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

In the next cell by changing the t<sub>0</sub> value you can correct the position of H<sub>1</sub> or any other known peak. this correction would be helpful for the position of the peaks in the m/c calibration process.
</div>

In [36]:
helper_t_0_tune.call_fine_tune_t_0(variables, flight_path_length, pulse_mode, t0)

Output()

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

Remove the data with m/c greater than max m/c and x, y, t = 0. Also add the needed colums for calibration. The data types of the final cropped dataset is displayed below.

</div>

In [11]:
# add the columns in the dataset for x, y, z, mc, mc calibrated, and t calibrated
helper_data_loader.add_columns(variables, max_mc)

display(variables.data)
display(variables.data.dtypes)

The number of data over max_mc: 681286
The number of data with having t, x, and y equal to zero is: 0


x (nm)  y (nm)  z (nm)  mc_c (Da)    mc (Da)  high_voltage (V)  \
0            0.0     0.0     0.0        0.0  29.892966       5028.560059   
1            0.0     0.0     0.0        0.0  29.438919       5028.560059   
2            0.0     0.0     0.0        0.0  29.262705       5028.560059   
3            0.0     0.0     0.0        0.0  29.393202       5028.560059   
4            0.0     0.0     0.0        0.0  29.917120       5028.560059   
...          ...     ...     ...        ...        ...               ...   
10037799     0.0     0.0     0.0        0.0  30.519060       6347.270020   
10037800     0.0     0.0     0.0        0.0  28.771356       6347.270020   
10037801     0.0     0.0     0.0        0.0  29.213997       6347.270020   
10037802     0.0     0.0     0.0        0.0  29.914848       6347.270020   
10037803     0.0     0.0     0.0        0.0  29.899011       6347.270020   

                pulse  start_counter  t_c (ns)      t (ns)  x_det (cm)  \
0         1005.711975          17740       0.0  614.915710    0.943673   
1         1005.711975          18142       0.0  625.381042    1.822041   
2         1005.711975          18382       0.0  614.181885    2.426122   
3         1005.711975          18721       0.0  616.733093    1.678367   
4         1005.711975          19550       0.0  608.242859   -0.653061   
...               ...            ...       ...         ...         ...   
10037799  1269.453979           7993       0.0  552.309021   -0.839184   
10037800  1269.453979           8008       0.0  557.966858    3.382857   
10037801  1269.453979           8031       0.0  550.327087    2.174694   
10037802  1269.453979           8309       0.0  550.512207   -0.937143   
10037803  1269.453979           8328       0.0  547.186096   -0.375510   

          y_det (cm)  pulse_pi  ion_pp  
0           1.730612         0       0  
1           2.671021       402       2  
2           0.604082       240       1  
3           1.998367       339       1  
4           0.698776       829       1  
...              ...       ...     ...  
10037799    1.002449        90       1  
10037800   -0.773878        15       1  
10037801    1.214694        23       1  
10037802   -1.560816       278       1  
10037803    1.276735        19       1  

[10037804 rows x 14 columns]

x (nm)              float64
y (nm)              float64
z (nm)              float64
mc_c (Da)           float64
mc (Da)             float64
high_voltage (V)    float64
pulse               float64
start_counter        uint32
t_c (ns)            float64
t (ns)              float64
x_det (cm)          float64
y_det (cm)          float64
pulse_pi             uint32
ion_pp               uint32
dtype: object

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Time-of-Flight Calibration Workflow

</div>

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
Below you can plot the ToF histogram of the dataset. You can select the peak range of the data you want to plot by drawing a rectangle over peak with holding left click. After that you should apply the voltage and bowl calibration. These three steps should be repeated until you see no improvement in the peak resolution. You can also save the calibration by clicking on the save button. The saved calibration will be used for the next steps.

</div>

In [12]:
# exctract needed data from Pandas data frame as an numpy array
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)
calibration_mode = widgets.Dropdown(
    options=[('time_of_flight', 'tof'), ('mass_to_charge', 'mc')],
    description='calibration mode:')
display(calibration_mode)

The maximum time of flight: 5010


Dropdown(description='calibration mode:', options=(('time_of_flight', 'tof'), ('mass_to_charge', 'mc')), value…

In [32]:
helper_voltage_bowl.call_voltage_bowl_calibration(variables, det_diam, flight_path_length, max_mc, calibration_mode)

Output()

In [37]:
helper_ion_list.call_ion_list(variables, selector='peak', calibration_mode=calibration_mode)

In [38]:
helper_mc_plot.call_mc_plot(variables, selector='None')

Output()

In [17]:
variables.data['mc_c (Da)'] = variables.mc_calib
variables.data['t_c (ns)'] = variables.dld_t_calib
# Remove negative mc
threshold = 0
mc_t = variables.data['mc_c (Da)'].to_numpy()
mc_t_mask = (mc_t <= threshold)
print('The number of ions with negative mc are:', len(mc_t_mask[mc_t_mask==True]))
variables.data.drop(np.where(mc_t_mask)[0], inplace=True)
variables.data.reset_index(inplace=True, drop=True)

The number of ions with negative mc are: 10091


-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## 3D Reconstruction Workflow

After bowl and voltage calibration we are ready to calculate the 3d reconstruction. In this workflow we calculate the reconstructed x,y,z and then plot the 3d, heatmap, projection plots and mass-to-charge histogram.

</div>

In [18]:
# exctract needed data from Pandas data frame as an numpy array
data_tools.extract_data(variables.data, variables, flight_path_length.value, max_mc.value)

display(variables.data)

The maximum time of flight: 5010


x (nm)  y (nm)  z (nm)  mc_c (Da)    mc (Da)  high_voltage (V)  \
0            0.0     0.0     0.0  27.297714  29.892966       5028.560059   
1            0.0     0.0     0.0  27.089858  29.438919       5028.560059   
2            0.0     0.0     0.0  27.156337  29.262705       5028.560059   
3            0.0     0.0     0.0  27.021961  29.393202       5028.560059   
4            0.0     0.0     0.0  27.021114  29.917120       5028.560059   
...          ...     ...     ...        ...        ...               ...   
10027708     0.0     0.0     0.0  27.443954  30.519060       6347.270020   
10027709     0.0     0.0     0.0  26.973540  28.771356       6347.270020   
10027710     0.0     0.0     0.0  26.951441  29.213997       6347.270020   
10027711     0.0     0.0     0.0  27.211502  29.914848       6347.270020   
10027712     0.0     0.0     0.0  26.961593  29.899011       6347.270020   

                pulse  start_counter    t_c (ns)      t (ns)  x_det (cm)  \
0         1005.711975          17740  566.961530  614.915710    0.943673   
1         1005.711975          18142  564.934474  625.381042    1.822041   
2         1005.711975          18382  565.583629  614.181885    2.426122   
3         1005.711975          18721  564.270652  616.733093    1.678367   
4         1005.711975          19550  564.262368  608.242859   -0.653061   
...               ...            ...         ...         ...         ...   
10027708  1269.453979           7993  568.383091  552.309021   -0.839184   
10027709  1269.453979           8008  563.796736  557.966858    3.382857   
10027710  1269.453979           8031  563.580301  550.327087    2.174694   
10027711  1269.453979           8309  566.121712  550.512207   -0.937143   
10027712  1269.453979           8328  563.679740  547.186096   -0.375510   

          y_det (cm)  pulse_pi  ion_pp  
0           1.730612         0       0  
1           2.671021       402       2  
2           0.604082       240       1  
3           1.998367       339       1  
4           0.698776       829       1  
...              ...       ...     ...  
10027708    1.002449        90       1  
10027709   -0.773878        15       1  
10027710    1.214694        23       1  
10027711   -1.560816       278       1  
10027712    1.276735        19       1  

[10027713 rows x 14 columns]

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

You have to select the main element in your sample from the from dropdown below.
</div>

In [19]:
element_selected = wd.density_field_selection()
display(element_selected)

Dropdown(description='Element', options=((1, 'H', 52.7, 0.0), (2, 'He', 28.7, 0.0), (3, 'Li', 46.3, 14.0), (4,…

In [21]:
helper_3d_reconstruction.call_x_y_z_calculation(variables, flight_path_length, element_selected)

Output()

In [ ]:
variables.data['x (nm)'] = variables.x
variables.data['y (nm)'] = variables.y
variables.data['z (nm)'] = variables.z

x (nm)     y (nm)     z (nm)   mc_c (Da)     mc (Da)  \
0         -1.530969  21.011234   3.453529   27.421958   29.956084   
1         21.111801 -17.469183   5.959122   26.289836   28.719354   
2         -2.590343   7.852830   0.520206   13.692070   14.957392   
3         24.651282   4.722667   4.960399   26.499332   28.948208   
4         10.239637 -21.938357   4.602177   13.441570   14.683738   
...             ...        ...        ...         ...         ...   
11093088 -21.798838  -0.609284  31.404541  212.582537  232.215267   
11093089  13.023875  13.126156  30.579931   27.006755   29.502517   
11093090 -30.213689   2.245389  34.196237   27.970186   30.554968   
11093091 -10.227634  17.329213  30.967547   27.621337   30.173886   
11093092   6.311887  -9.071181  29.241632   13.499378   14.746890   

          high_voltage (V)        pulse  start_counter    t_c (ns)  \
0              5014.649902  1002.929993          16917   30.193781   
1              5014.649902  1002.929993          17140   28.947238   
2              5014.649902  1002.929993          17216   15.076077   
3              5014.649902  1002.929993          17297   29.177908   
4              5014.649902  1002.929993          17466   14.800251   
...                    ...          ...            ...         ...   
11093088       6347.439941  1269.488037          10162  233.460715   
11093089       6347.439941  1269.488037          10257   29.660749   
11093090       6347.439941  1269.488037          10299   30.718844   
11093091       6347.439941  1269.488037          10311   30.335719   
11093092       6347.439941  1269.488037          10328   14.825982   

               t (ns)  x_det (cm)  y_det (cm)  pulse_pi  ion_pp  
0          623.015015   -0.189388    2.599184         0       0  
1          622.733826    2.687347   -2.223674       223       2  
2          441.874664   -0.310204    0.940408        76       1  
3          620.210083    3.102041    0.594286        81       1  
4          451.434723    1.283265   -2.749388       127       1  
...               ...         ...         ...       ...     ...  
11093088  1472.275391   -2.102857   -0.058776       133       1  
11093089   546.596313    1.247347    1.257143        95       1  
11093090   567.622925   -2.987755    0.222041        42       1  
11093091   553.598328   -0.982857    1.665306        12       1  
11093092   394.609314    0.597551   -0.858775        17       1  

[11093093 rows x 14 columns]

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">

## Ion Selection and Rangging

This tutorial outlines a comprehensive workflow for ion selection and organization. Users can choose ions using peak and element finders, manually add ions, customize ion colors, and create histograms. Histograms can be generated for selected ranges and areas, and figures can be saved. Additionally, users have the option to save both figures and data in CSV and HDF5 formats.

</div>

In [34]:
# exctract needed data from Pandas data frame as an numpy array
data_tools.extract_data(variables.data, variables, flightPathLength.value, max_mc.value)

display(variables.data)

The maximum time of flight: 5010


x (nm)     y (nm)     z (nm)   mc_c (Da)     mc (Da)  \
0         -1.530969  21.011234   3.453529   27.421958   29.956084   
1         21.111801 -17.469183   5.959122   26.289836   28.719354   
2         -2.590343   7.852830   0.520206   13.692070   14.957392   
3         24.651282   4.722667   4.960399   26.499332   28.948208   
4         10.239637 -21.938357   4.602177   13.441570   14.683738   
...             ...        ...        ...         ...         ...   
11093088 -21.798838  -0.609284  31.404541  212.582537  232.215267   
11093089  13.023875  13.126156  30.579931   27.006755   29.502517   
11093090 -30.213689   2.245389  34.196237   27.970186   30.554968   
11093091 -10.227634  17.329213  30.967547   27.621337   30.173886   
11093092   6.311887  -9.071181  29.241632   13.499378   14.746890   

          high_voltage (V)        pulse  start_counter    t_c (ns)  \
0              5014.649902  1002.929993          16917   30.193781   
1              5014.649902  1002.929993          17140   28.947238   
2              5014.649902  1002.929993          17216   15.076077   
3              5014.649902  1002.929993          17297   29.177908   
4              5014.649902  1002.929993          17466   14.800251   
...                    ...          ...            ...         ...   
11093088       6347.439941  1269.488037          10162  233.460715   
11093089       6347.439941  1269.488037          10257   29.660749   
11093090       6347.439941  1269.488037          10299   30.718844   
11093091       6347.439941  1269.488037          10311   30.335719   
11093092       6347.439941  1269.488037          10328   14.825982   

               t (ns)  x_det (cm)  y_det (cm)  pulse_pi  ion_pp  
0          623.015015   -0.189388    2.599184         0       0  
1          622.733826    2.687347   -2.223674       223       2  
2          441.874664   -0.310204    0.940408        76       1  
3          620.210083    3.102041    0.594286        81       1  
4          451.434723    1.283265   -2.749388       127       1  
...               ...         ...         ...       ...     ...  
11093088  1472.275391   -2.102857   -0.058776       133       1  
11093089   546.596313    1.247347    1.257143        95       1  
11093090   567.622925   -2.987755    0.222041        42       1  
11093091   553.598328   -0.982857    1.665306        12       1  
11093092   394.609314    0.597551   -0.858775        17       1  

[11093093 rows x 14 columns]

In [32]:
helper_ion_selection.call_ion_selection(variables)

In [33]:
variables.range_data

ion  mass   mc  mc_low  mc_up    color   element complex isotope  \
0  unranged   0.0  0.0     0.0  400.0  #000000  unranged       0       0   

   charge  
0       0

In [34]:
variables.range_data.dtypes

ion         object
mass       float64
mc         float64
mc_low     float64
mc_up      float64
color       object
element     object
complex     object
isotope     object
charge      uint32
dtype: object

-------------------------------------------------------
-------------------------------------------------------

<div style="margin: 0 auto; padding: 20px; font-family: 'Helvetica', sans-serif; font-size: 16px;">
    
# Visualization
    
</div>

In [18]:
helper_visualization.call_visualization(variables)

Output()

In [ ]:
from pyccapt.calibration.reconstructions import reconstruction

reconstruction.reconstruction_plot(variables, element_percentage=[0.001, 0.001, 0.001], opacity=0.5, rotary_fig_save=False, selected_area_specially=False,
                        selected_area_temporally=False, figname='22', save=False, ions_individually_plots=True)